In [30]:
# Colab: interaktywny czytnik plików METEO + wykresy
# Przeznaczenie: folder /content/drive/MyDrive/METEO/
# Struktura katalogów: METEO/MMYYYY/DDMMYYYYmeteo.dat (jedna stacja)
# Format pliku .dat: whitespace-separated columns
# year month day hour min sec wind_speed wind_dir temp RH pressure suma_opadu natezenie_opadu

# -----------------------------
# 0. Instalacje / importy
# -----------------------------
!pip install ipywidgets --quiet

from google.colab import drive
import os, glob
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from IPython.display import display, clear_output
import ipywidgets as widgets
from datetime import datetime
import matplotlib.dates as mdates

plt.rcParams["figure.figsize"] = (12,6)

# -----------------------------
# 1. Montowanie Google Drive
# -----------------------------
drive.mount('/content/drive')

# base folder (zmień jeśli trzeba)
BASE_DIR = "/content/drive/MyDrive/LO_Strzyzow/METEO"
#filepath="/content/drive/MyDrive/LO_Strzyzow/METEO"
#BASE_DIR = "/content/drive/MyDrive/LO_Strzyzow"
if not os.path.exists(BASE_DIR):
    raise FileNotFoundError(f"Nie znaleziono katalogu METEO pod: {BASE_DIR}")

# -----------------------------
# 2. Przygotowanie listy miesięcy (katalogów MMYYYY)
# -----------------------------
months = sorted([d for d in os.listdir(BASE_DIR) if os.path.isdir(os.path.join(BASE_DIR, d))])
if not months:
    raise FileNotFoundError(f"Brak podkatalogów w {BASE_DIR}. Struktura powinna być METEO/MMYYYY/...")

# Widgety: dropdown miesiąca i pliku oraz przycisk "Wczytaj i rysuj"
month_dd = widgets.Dropdown(options=months, description='Miesiąc (MMYYYY):')
file_dd = widgets.Dropdown(options=[''], description='Plik:')
load_btn = widgets.Button(description='Wczytaj i Rysuj', button_style='primary')

out = widgets.Output()

# -----------------------------
# 3. Funkcja pomocnicza: lista plików w wybranym miesiącu
# -----------------------------
def list_files_for_month(month):
    folder = os.path.join(BASE_DIR, month)
    # pliki kończące się na meteo.dat (case-insensitive)
    files = sorted([f for f in os.listdir(folder) if f.lower().endswith('vaisala.dat')])
    return files

# -----------------------------
# 4. Zmiana listy plików po wyborze miesiąca
# -----------------------------
def on_month_change(change):
    if change['name']=='value':
        m = change['new']
        files = list_files_for_month(m)
        if not files:
            file_dd.options = ['Brak plików']
        else:
            file_dd.options = files

month_dd.observe(on_month_change)

# inicjalizacja plików dla pierwszego miesiąca
file_dd.options = list_files_for_month(months[0]) if months else ['Brak plików']

# -----------------------------
# 5. Wczytywanie pliku .dat i rysowanie wykresów
# -----------------------------

col_names = [
    "day", "month", "year", "hour", "minute", "second","wind_dir1","wind_dir2",
    "wind_dir3","wind_min", "wind_mean", "wind_max","temp", "RH", "pressure",
    "rain_sum","rain_time", "rain_intensity", "grain_sum","grain_intensity","voltage1",
    "vol2","volt3","volt4"
]
#df = pd.read_csv(filepath, delim_whitespace=True, names=col_names, header=None)

def read_meteo_file(path):
    """
    Wczytuje plik whitespace-separated, próbuje odczytać bez nagłówka.
    Jeśli plik ma nagłówek (nazwy kolumn), pd.read_csv automatycznie wykryje.
    """
    # najpierw spróbuj wczytać automatycznie
    try:
        df = pd.read_csv(path, sep=r'\s+', comment='#', engine='python')
        # jeśli wykryty nagłówek nie pasuje do oczekiwanej liczby kolumn, wczytaj z nazwami
        if df.shape[1] not in [len(col_names), len(col_names)-1, len(col_names)+1]:
            df = pd.read_csv(path, sep=r'\s+', names=col_names, header=None, engine='python')
    except Exception:
        # fallback: wymuszenie nazw kolumn
        df = pd.read_csv(path, sep=r'\s+', names=col_names, header=None, engine='python')
    # jeśli więcej kolumn wykryto niż oczekiwane - obetnij nadmiar
    if df.shape[1] > len(col_names):
        df = df.iloc[:, :len(col_names)]
        df.columns = col_names
    # gdy mniej kolumn - uzupełnij brakujące
    if df.shape[1] < len(col_names):
        for i,cn in enumerate(col_names):
            if i >= df.shape[1]:
                df[cn] = np.nan
    df = df[col_names]  # uporządkuj
    return df

def process_and_plot(month, filename):
    folder = os.path.join(BASE_DIR, month)
    path = os.path.join(folder, filename)

    if not os.path.exists(path):
        with out:
            clear_output()
            print("Nie znaleziono pliku:", path)
        return

    # --------------------------
    # Wczytanie pliku dynamicznie
    # --------------------------
    try:
        df_raw = pd.read_csv(path, delim_whitespace=True, header=None, engine='python')
    except Exception as e:
        with out:
            clear_output()
            print("Błąd wczytywania pliku:", e)
        return

    n_cols = df_raw.shape[1]
    col_names_dynamic = [f"col{i+1}" for i in range(n_cols)]
    df_raw.columns = col_names_dynamic

    # --------------------------
    # Mapowanie kolumn na sensowne nazwy
    # --------------------------
    col_map = {
        'col1':'day', 'col2':'month','col3':'year','col4':'hour','col5':'minute','col6':'second',
        'col7':'wind_dir1','col8':'wind_dir2','col9':'wind_dir3',
        'col10':'wind_min','col11':'wind_mean','col12':'wind_max',
        'col13':'temp','col14':'RH','col15':'pressure',
        'col16':'rain_sum','col17':'rain_time','col18':'rain_intensity',
        'col19':'grain_sum','col20':'grain_intensity','col21':'voltage1'
    }
    # zmień tylko kolumny, które istnieją
    df = df_raw.rename(columns={k:v for k,v in col_map.items() if k in df_raw.columns})

    # --------------------------
    # Konwersja typów liczbowych
    # --------------------------
    for c in df.columns:
        if c not in ['day','month','year','hour','minute','second']:
            df[c] = pd.to_numeric(df[c], errors='coerce')

    # --------------------------
    # Stworzenie kolumny datetime
    # --------------------------
    try:
        df['datetime'] = pd.to_datetime(df[['day','month','year','hour','minute','second']], errors='coerce', utc=True)
    except Exception as e:
        with out:
            clear_output()
            print("Błąd konwersji daty:", e)
        df['datetime'] = pd.NaT

    df.set_index('datetime', inplace=True, drop=False)

    # --------------------------
    # Wyświetlenie podstawowych informacji
    # --------------------------
    with out:
        clear_output()
        print(f"Wczytano: {path}")
        print("Zakres czasowy danych:", df['datetime'].min(), "->", df['datetime'].max())
        print("Liczba wierszy:", len(df))
        print("Dostępne kolumny:", list(df.columns))

        # --------------------------
        # Wykresy
        # --------------------------
        fig, axes = plt.subplots(3,2, figsize=(14,12))
        ax1, ax2, ax3, ax4, ax5, ax6 = axes.flatten()

        # Temperatura
        if 'temp' in df.columns:
            ax1.plot(df.index, df['temp'], marker='.', linewidth=0.8)
            ax1.set_title('Temperatura (°C)')
            ax1.set_ylabel('°C')
            ax1.grid(True)
        else:
            ax1.text(0.5,0.5,"Brak kolumny temp", ha='center')

        # Wilgotność
        if 'RH' in df.columns:
            ax2.plot(df.index, df['RH'], marker='.', linewidth=0.8)
            ax2.set_title('Wilgotność względna (%)')
            ax2.set_ylabel('%')
            ax2.grid(True)

        # Ciśnienie
        if 'pressure' in df.columns:
            ax3.plot(df.index, df['pressure'], marker='.', linewidth=0.8)
            ax3.set_title('Ciśnienie (hPa)')
            ax3.set_ylabel('hPa')
            ax3.grid(True)

        # Wiatr (speed + kierunek)
        if 'wind_mean' in df.columns:
            ax4.plot(df.index, df['wind_mean'], marker='.', linewidth=0.8, label='wind speed')
            if 'wind_dir1' in df.columns:
                sc = ax4.scatter(df.index, df['wind_mean'], c=df['wind_dir1'], cmap='hsv', s=20, label='dir')
                cbar = fig.colorbar(sc, ax=ax4, orientation='vertical', pad=0.02)
                cbar.set_label('Kierunek wiatru (deg)')
            ax4.set_title('Prędkość wiatru (m/s)')
            ax4.set_ylabel('m/s')
            ax4.grid(True)

        # Suma opadu
        if 'rain_intensity' in df.columns:
            ax5.step(df.index, df['rain_intensity'], marker='.',linewidth=0.8, label='rain')
            ax5.set_title('Natężenie opadu')
            ax5.set_ylabel('mm/h')
            ax5.grid(True)

        if 'rain_sum' in df.columns:
            ax6.step(df.index, df['rain_sum']-df['rain_sum'].iloc[0], marker='.',linewidth=0.8, label='rain')
            ax6.set_title('Suma opadu')
            ax6.set_ylabel('mm')
            ax6.grid(True)

        #ax6.axis('off')  # dla spokoju, pusta oś
        ax1.xaxis.set_major_formatter(mdates.DateFormatter('%H:%M'))
        ax2.xaxis.set_major_formatter(mdates.DateFormatter('%H:%M'))
        ax3.xaxis.set_major_formatter(mdates.DateFormatter('%H:%M'))
        ax4.xaxis.set_major_formatter(mdates.DateFormatter('%H:%M'))
        ax5.xaxis.set_major_formatter(mdates.DateFormatter('%H:%M'))
        ax6.xaxis.set_major_formatter(mdates.DateFormatter('%H:%M'))
        plt.tight_layout()
        plt.show()

        # Statystyki
        print("\nPodstawowe statystyki (kolumny numeryczne):")
        display(df.describe().T)
# -----------------------------
# 6. Handler przycisku
# -----------------------------
def on_load_clicked(b):
    m = month_dd.value
    f = file_dd.value
    if (not m) or (not f) or f.lower().startswith('brak'):
        with out:
            clear_output()
            print("Wybierz poprawny miesiąc i plik.")
        return
    process_and_plot(m, f)

load_btn.on_click(on_load_clicked)

# -----------------------------
# 7. Wyświetlenie widgetów
# -----------------------------
display(widgets.HBox([month_dd, file_dd, load_btn]))
display(out)

# Instrukcja dla użytkownika:
print("Wybierz miesiąc, potem plik z listy i kliknij 'Wczytaj i Rysuj'.")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


Output()

Wybierz miesiąc, potem plik z listy i kliknij 'Wczytaj i Rysuj'.


/tmp/ipython-input-3620237662.py:128: FutureWarning: The 'delim_whitespace' keyword in pd.read_csv is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  df_raw = pd.read_csv(path, delim_whitespace=True, header=None, engine='python')
